In [1]:
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import os
import plotly.io as pio

from scipy import stats
from scipy.special import gammainc, gammaln, psi

pio.templates.default = "plotly_white"
pio.renderers.default = os.environ.get("PLOTLY_RENDERER", "notebook")
np.set_printoptions(precision=4, suppress=True)

rng = np.random.default_rng(42)

In [2]:
def gamma_logpdf(x, alpha, theta):
    """Log-PDF of Gamma(alpha, theta) with support (0, inf)."""
    x = np.asarray(x, dtype=float)
    alpha = float(alpha)
    theta = float(theta)
    if alpha <= 0 or theta <= 0:
        raise ValueError("alpha and theta must be > 0")

    logpdf = np.full_like(x, -np.inf, dtype=float)
    mask = x > 0
    logpdf[mask] = (
        (alpha - 1) * np.log(x[mask]) - x[mask] / theta - gammaln(alpha) - alpha * np.log(theta)
    )
    return logpdf


def gamma_pdf(x, alpha, theta):
    return np.exp(gamma_logpdf(x, alpha, theta))


def gamma_cdf(x, alpha, theta):
    """CDF via the regularized lower incomplete gamma P(alpha, x/theta)."""
    x = np.asarray(x, dtype=float)
    alpha = float(alpha)
    theta = float(theta)
    if alpha <= 0 or theta <= 0:
        raise ValueError("alpha and theta must be > 0")

    cdf = np.zeros_like(x, dtype=float)
    mask = x > 0
    cdf[mask] = gammainc(alpha, x[mask] / theta)
    return cdf


def gamma_entropy(alpha, theta):
    """Differential entropy of Gamma(alpha, theta)."""
    alpha = float(alpha)
    theta = float(theta)
    if alpha <= 0 or theta <= 0:
        raise ValueError("alpha and theta must be > 0")

    return alpha + np.log(theta) + gammaln(alpha) + (1 - alpha) * psi(alpha)


def gamma_mgf(t, alpha, theta):
    """MGF M_X(t) for t < 1/theta; diverges for t >= 1/theta."""
    t = np.asarray(t, dtype=float)
    alpha = float(alpha)
    theta = float(theta)
    if alpha <= 0 or theta <= 0:
        raise ValueError("alpha and theta must be > 0")

    out = np.full_like(t, np.inf, dtype=float)
    mask = t < 1 / theta
    out[mask] = (1 - theta * t[mask]) ** (-alpha)
    return out


def gamma_cf(t, alpha, theta):
    """Characteristic function phi_X(t)."""
    t = np.asarray(t, dtype=float)
    alpha = float(alpha)
    theta = float(theta)
    if alpha <= 0 or theta <= 0:
        raise ValueError("alpha and theta must be > 0")

    return (1 - 1j * theta * t) ** (-alpha)

In [3]:
alpha, theta = 2.5, 1.3

mean_theory = alpha * theta
var_theory = alpha * theta**2
skew_theory = 2 / np.sqrt(alpha)
excess_kurt_theory = 6 / alpha
entropy_theory = gamma_entropy(alpha, theta)

mean_theory, var_theory, skew_theory, excess_kurt_theory, entropy_theory

(3.25, 4.2250000000000005, 1.2649110640673518, 2.4, 1.9923121739725458)

In [4]:
# PDF: changing shape alpha (keep theta fixed)
theta_fixed = 1.0
alphas = [0.5, 1.0, 2.0, 5.0]

x = np.linspace(1e-6, 12, 600)
fig = go.Figure()
for a in alphas:
    fig.add_trace(
        go.Scatter(
            x=x,
            y=gamma_pdf(x, a, theta_fixed),
            mode="lines",
            name=f"α={a:g}, θ={theta_fixed:g}",
        )
    )

fig.update_layout(
    title="Gamma PDF: effect of the shape α (scale θ=1)",
    xaxis_title="x",
    yaxis_title="pdf",
)
fig.show()

In [5]:
# PDF: changing scale theta (keep alpha fixed)
alpha_fixed = 2.0
thetas = [0.5, 1.0, 2.0]

x = np.linspace(1e-6, 20, 700)
fig = go.Figure()
for th in thetas:
    fig.add_trace(
        go.Scatter(
            x=x,
            y=gamma_pdf(x, alpha_fixed, th),
            mode="lines",
            name=f"α={alpha_fixed:g}, θ={th:g}",
        )
    )
    fig.add_vline(
        x=alpha_fixed * th,
        line_dash="dot",
        annotation_text=f"mean={alpha_fixed * th:.2f}",
        annotation_position="top",
    )

fig.update_layout(
    title="Gamma PDF: effect of the scale θ (shape α=2)",
    xaxis_title="x",
    yaxis_title="pdf",
)
fig.show()

In [6]:
def gamma_loglik(x, alpha, theta):
    x = np.asarray(x, dtype=float)
    alpha = float(alpha)
    theta = float(theta)
    if alpha <= 0 or theta <= 0:
        return -np.inf
    if np.any(x <= 0):
        return -np.inf

    n = x.size
    return (
        (alpha - 1) * np.sum(np.log(x))
        - np.sum(x) / theta
        - n * (gammaln(alpha) + alpha * np.log(theta))
    )


# Quick sanity check: theta-hat given alpha
alpha_true, theta_true = 3.0, 1.5
x = stats.gamma(a=alpha_true, scale=theta_true).rvs(size=2000, random_state=rng)

theta_hat_if_alpha_known = x.mean() / alpha_true
theta_hat_if_alpha_known, theta_true

(1.5106385112629404, 1.5)

In [7]:
def _gamma_rvs_mt_shape_ge_1(alpha, n, rng):
    """Marsaglia–Tsang sampler for Gamma(alpha, 1) with alpha >= 1."""
    d = alpha - 1.0 / 3.0
    c = 1.0 / np.sqrt(9.0 * d)

    out = np.empty(n, dtype=float)
    filled = 0
    while filled < n:
        m = n - filled

        z = rng.normal(size=m)
        v = (1.0 + c * z) ** 3

        valid = v > 0
        if not np.any(valid):
            continue

        z = z[valid]
        v = v[valid]
        u = rng.random(size=v.size)

        # Squeeze step + main acceptance test
        accept = (u < 1.0 - 0.0331 * (z**4)) | (
            np.log(u) < 0.5 * z**2 + d * (1.0 - v + np.log(v))
        )

        accepted = d * v[accept]
        k = accepted.size
        out[filled : filled + k] = accepted
        filled += k

    return out


def gamma_rvs_numpy(alpha, theta=1.0, size=1, rng=None):
    """Sample from Gamma(alpha, theta) using NumPy only.

    Parameters
    ----------
    alpha : float
        Shape parameter (> 0).
    theta : float
        Scale parameter (> 0).
    size : int or tuple
        Output shape.
    rng : np.random.Generator
        Random number generator.
    """
    if rng is None:
        rng = np.random.default_rng()

    alpha = float(alpha)
    theta = float(theta)
    if alpha <= 0 or theta <= 0:
        raise ValueError("alpha and theta must be > 0")

    size_tuple = (size,) if isinstance(size, int) else tuple(size)
    n = int(np.prod(size_tuple))

    if alpha >= 1:
        x = _gamma_rvs_mt_shape_ge_1(alpha, n, rng)
    else:
        # Boost shape to alpha+1 >= 1, then apply the U^(1/alpha) correction
        y = _gamma_rvs_mt_shape_ge_1(alpha + 1.0, n, rng)
        u = rng.random(size=n)
        x = y * (u ** (1.0 / alpha))

    return (x * theta).reshape(size_tuple)


# Smoke test: mean/variance roughly match theory
alpha_test, theta_test = 2.5, 1.3
s = gamma_rvs_numpy(alpha_test, theta_test, size=50_000, rng=rng)
s.mean(), (alpha_test * theta_test), s.var(), (alpha_test * theta_test**2)

(3.2476485440524825, 3.25, 4.233222259786438, 4.2250000000000005)

In [8]:
def ecdf(samples):
    x = np.sort(np.asarray(samples))
    y = np.arange(1, x.size + 1) / x.size
    return x, y


alpha_viz, theta_viz = 2.5, 1.3
n_viz = 80_000

samples = gamma_rvs_numpy(alpha_viz, theta_viz, size=n_viz, rng=rng)
x_max = float(np.quantile(samples, 0.995))
x_grid = np.linspace(1e-6, x_max, 600)

# PDF + histogram
fig = go.Figure()
fig.add_trace(
    go.Histogram(
        x=samples,
        nbinsx=70,
        histnorm="probability density",
        name="Monte Carlo samples",
        opacity=0.55,
    )
)
fig.add_trace(
    go.Scatter(
        x=x_grid,
        y=gamma_pdf(x_grid, alpha_viz, theta_viz),
        mode="lines",
        name="Theoretical PDF",
        line=dict(width=3),
    )
)
fig.update_layout(
    title=f"Gamma(α={alpha_viz:g}, θ={theta_viz:g}): histogram vs PDF",
    xaxis_title="x",
    yaxis_title="density",
    bargap=0.02,
)
fig.show()

# CDF + empirical CDF
xs, ys = ecdf(samples)

fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x=x_grid,
        y=gamma_cdf(x_grid, alpha_viz, theta_viz),
        mode="lines",
        name="Theoretical CDF",
        line=dict(width=3),
    )
)
fig.add_trace(
    go.Scatter(
        x=xs[::100],
        y=ys[::100],
        mode="markers",
        name="Empirical CDF (subsampled)",
        marker=dict(size=5),
    )
)
fig.update_layout(
    title=f"Gamma(α={alpha_viz:g}, θ={theta_viz:g}): empirical CDF vs CDF",
    xaxis_title="x",
    yaxis_title="CDF",
)
fig.show()

# Monte Carlo moment check
sample_mean = samples.mean()
sample_var = samples.var()
theory_mean = alpha_viz * theta_viz
theory_var = alpha_viz * theta_viz**2

sample_mean, theory_mean, sample_var, theory_var

(3.2598087590265608, 3.25, 4.286106165978027, 4.2250000000000005)

In [9]:
alpha_true, theta_true = 3.0, 1.5

dist = stats.gamma(a=alpha_true, loc=0, scale=theta_true)

x = np.linspace(0, 15, 500)
pdf = dist.pdf(x)
cdf = dist.cdf(x)

samples_scipy = dist.rvs(size=5000, random_state=rng)

# MLE fit (note: constrain loc=0 to match the usual Gamma support)
a_hat, loc_hat, scale_hat = stats.gamma.fit(samples_scipy, floc=0)
a_hat, loc_hat, scale_hat

(2.970249528831039, 0, 1.5243399321816582)

In [10]:
# A) Hypothesis testing example: Exponential (alpha=1) vs Gamma (alpha free)

# Generate data from a Gamma alternative
alpha_data, theta_data = 2.0, 2.0
data = stats.gamma(a=alpha_data, scale=theta_data).rvs(size=2500, random_state=rng)

# Fit the unrestricted Gamma
a_hat, loc_hat, scale_hat = stats.gamma.fit(data, floc=0)

# Null model: alpha = 1 (exponential). MLE for theta is just the sample mean.
theta0_hat = data.mean()

ll_null = gamma_loglik(data, alpha=1.0, theta=theta0_hat)
ll_alt = gamma_loglik(data, alpha=a_hat, theta=scale_hat)

lr_stat = 2 * (ll_alt - ll_null)
p_value_lrt = stats.chi2.sf(lr_stat, df=1)

# Goodness-of-fit (KS) for the fitted Gamma
D_ks, p_value_ks = stats.kstest(data, "gamma", args=(a_hat, 0, scale_hat))

lr_stat, p_value_lrt, D_ks, p_value_ks

(601.8915919589344,
 6.491780106731331e-133,
 0.01017051215045639,
 0.9558863897485597)

In [11]:
# B) Bayesian modeling: Gamma prior for a Poisson rate
# Use rate parameterization for the prior/posterior: Gamma(α, β) with mean α/β.

alpha0, beta0 = 2.0, 1.0
lambda_true = 3.0
n = 25

y = rng.poisson(lam=lambda_true, size=n)

alpha_post = alpha0 + y.sum()
beta_post = beta0 + n

# Convert rate β to scale θ=1/β for our Gamma(alpha, theta) helper functions
lam_grid = np.linspace(1e-6, max(10, 3 * lambda_true), 600)
prior_pdf = gamma_pdf(lam_grid, alpha0, theta=1 / beta0)
post_pdf = gamma_pdf(lam_grid, alpha_post, theta=1 / beta_post)

fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x=lam_grid,
        y=prior_pdf,
        mode="lines",
        name=f"prior Γ(α={alpha0:g}, β={beta0:g})",
        line=dict(width=3),
    )
)
fig.add_trace(
    go.Scatter(
        x=lam_grid,
        y=post_pdf,
        mode="lines",
        name=f"posterior Γ(α={alpha_post:g}, β={beta_post:g})",
        line=dict(width=3),
    )
)
fig.add_vline(x=lambda_true, line_dash="dash", line_color="black", annotation_text="true λ")
fig.update_layout(
    title="Gamma–Poisson conjugacy: prior → posterior on λ",
    xaxis_title="λ",
    yaxis_title="density",
)
fig.show()

y.sum(), y.mean(), (alpha_post / beta_post)

(68, 2.72, 2.6923076923076925)

In [12]:
# C) Generative modeling: Poisson–Gamma mixture (overdispersed counts)

alpha_latent, theta_latent = 5.0, 0.6  # latent lambda ~ Gamma(alpha, theta)
n_obs = 20_000

lambdas = gamma_rvs_numpy(alpha_latent, theta_latent, size=n_obs, rng=rng)
counts_mixture = rng.poisson(lam=lambdas)

mean_counts = counts_mixture.mean()
counts_poisson = rng.poisson(lam=mean_counts, size=n_obs)

max_k = int(np.quantile(counts_mixture, 0.995))
bin_spec = dict(start=-0.5, end=max_k + 0.5, size=1)

fig = go.Figure()
fig.add_trace(
    go.Histogram(
        x=counts_mixture,
        xbins=bin_spec,
        histnorm="probability",
        name="Poisson–Gamma mixture",
        opacity=0.6,
    )
)
fig.add_trace(
    go.Histogram(
        x=counts_poisson,
        xbins=bin_spec,
        histnorm="probability",
        name="Poisson (same mean)",
        opacity=0.6,
    )
)
fig.update_layout(
    title="Overdispersion from a Poisson–Gamma mixture",
    xaxis_title="count",
    yaxis_title="probability",
    barmode="overlay",
)
fig.show()

counts_mixture.mean(), counts_mixture.var(), counts_poisson.var()

(2.98515, 4.7931294775, 2.9583533975000003)